In [3]:
from urllib.request import urlopen
from bs4 import BeautifulSoup
import re
from datetime import datetime, timedelta
from dateutil import parser
import time
import random
import pymongo
from dotenv import load_dotenv
import os
import scraper_faz

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.cluster import DBSCAN, KMeans
from sklearn.compose import make_column_transformer
from sklearn.datasets import load_sample_image, make_blobs
from sklearn.decomposition import PCA
from sklearn.ensemble import BaggingClassifier, BaggingRegressor, GradientBoostingClassifier, GradientBoostingRegressor, RandomForestClassifier, RandomForestRegressor, StackingClassifier, StackingRegressor
from sklearn.impute import KNNImputer, SimpleImputer
from sklearn.inspection import permutation_importance
from sklearn.linear_model import Lasso, LinearRegression, LogisticRegression, Ridge
from sklearn.manifold import Isomap, LocallyLinearEmbedding, MDS
from sklearn.metrics import auc, confusion_matrix, ConfusionMatrixDisplay, davies_bouldin_score, rand_score, roc_auc_score, roc_curve, silhouette_samples, silhouette_score 
from sklearn.model_selection import train_test_split, cross_validate, GridSearchCV
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier, KNeighborsRegressor
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, PolynomialFeatures, StandardScaler
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor, plot_tree
import statsmodels.api as sm
from ydata_profiling import ProfileReport

In [4]:
load_dotenv()
mongodb_uri = os.getenv("MONGODB_URI")
mongoclient = pymongo.MongoClient(mongodb_uri)
mongodb = mongoclient["media-scraper"]
mongo_execs = mongodb["executions"]
mongo_articles = mongodb["articles"]

In [7]:
df = pd.DataFrame(list(mongo_articles.find()))
df

_id                                           keywords  \
0     -gtn-bgvnd  [Bundesliga, Karlsruher SC, Hertha BSC Berlin,...   
1     -gr6-bhjvc  [Leonhard Dobusch, Volker Grassmuck, Elektra W...   
2     -gtn-bh4ww  [Lukas Daschner, Steffen Baumgart, Davie Selke...   
3     -gyc-bhi4z  [Amazon Alexa, Infotainment, Ladeplanung, Audi...   
4     -gs3-bhruw  [Francisco Peralta, Marionettenmuseum, Spanien...   
...          ...                                                ...   
3913  -gq5-bhvpt  [Fox News, Republikanische Partei, Tim Scott, ...   
3914  -gum-bhvok  [Neu Delhi, Vereinte Nationen, Indien, UNICEF,...   
3915  -gq5-bhvoi  [Reuters, Lloyd Austin, US-Militär, Syrien, US...   
3916  -gpg-bhvmg                                                NaN   
3917  -gzk-bhx0g  [Hermann Kretzschmar, Heinz Holliger, Péter Eö...   

      premiumArticle                   hrefPermalink          lastUpdate  \
0              False  https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
1              False  https://www.faz.net/-gr6-bhjvc 2023-11-11 21:13:00   
2              False  https://www.faz.net/-gtn-bh4ww 2023-11-11 20:55:16   
3              False  https://www.faz.net/-gyc-bhi4z 2023-11-11 20:50:45   
4              False  https://www.faz.net/-gs3-bhruw 2023-11-11 20:43:38   
...              ...                             ...                 ...   
3913           False  https://www.faz.net/-gq5-bhvpt 2023-11-13 03:45:57   
3914           False  https://www.faz.net/-gum-bhvok 2023-11-13 03:21:46   
3915           False  https://www.faz.net/-gq5-bhvoi 2023-11-13 02:29:58   
3916           False  https://www.faz.net/-gpg-bhvmg 2023-11-13 01:07:20   
3917            True  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   

                                                  title  \
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
1          Stefan Meys Buch „Der Kampf um das Internet“   
2     1. FC Köln bleibt nach Spiel in Bochum auf dem...   
3     Infotainment von Audi Q3 und Q4: Was zum Doppe...   
4                           Marionettenspiel in Spanien   
...                                                 ...   
3913  USA: Republikaner Tim Scott gibt Kandidatur um...   
3914  UNICEF: 347 Millionen Kindern in Südasien fehl...   
3915            USA bombardieren erneut Ziele in Syrien   
3916  Scholz will weiter mit Merz über Migration spr...   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   

                                              introText  \
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
1     Der entscheidende Kampf findet zwischen nachha...   
2     Die Ursachenforschung der Kölner geht nach dem...   
3     Das Infotainment des Audi Q3 und Q4 im Detail:...   
4     Kleist-Fantasie: Im spanischen Segovia gibt es...   
...                                                 ...   
3913  Außer Donald Trump sind jetzt nur noch vier Re...   
3914  In Ländern wie Indien leben besonders viele Ki...   
3915  Die Luftangriffe sind eine Reaktion auf Attack...   
3916  In einem Talkformat äußerte sich der Kanzler z...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   

                                             paragraphs  \
0     [Hertha BSC bleibt in der zweiten Fußball-Bund...   
1     [Nach gut dreißig Jahren des kommerziellen Int...   
2     [Die Last auf den Schultern der Kölner war all...   
3     [Das Infotainment in einem Audi ist mit dem Na...   
4     [Im Dezember 1810 erschien Kleists Aufsatz „Üb...   
...                                                 ...   
3913  [Der in Umfragen weit abgeschlagene US-Senator...   
3914  [In Südasien leiden weltweit am meisten Kinder...   
3915  [Die USA haben am Sonntag nach eigenen Angaben...   
3916  [Bundeskanzler Olaf Scholz (SPD) hat Oppositio...   
3917  [Happy New Ears!“ ist der Neujahrswunsch des K...   

                         source              author  \
0                   Quelle: sid                 NaN   
1         

In [19]:
df_exploded = df.explode("keywords").explode("paragraphs")
df_exploded

_id         keywords  premiumArticle  \
0     -gtn-bgvnd       Bundesliga           False   
0     -gtn-bgvnd       Bundesliga           False   
0     -gtn-bgvnd       Bundesliga           False   
0     -gtn-bgvnd       Bundesliga           False   
0     -gtn-bgvnd    Karlsruher SC           False   
...          ...              ...             ...   
3917  -gzk-bhx0g  Dietmar Wiesner            True   
3917  -gzk-bhx0g      Hans Zender            True   
3917  -gzk-bhx0g      Hans Zender            True   
3917  -gzk-bhx0g        John Cage            True   
3917  -gzk-bhx0g        John Cage            True   

                       hrefPermalink          lastUpdate  \
0     https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
0     https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
0     https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
0     https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
0     https://www.faz.net/-gtn-bgvnd 2023-11-11 22:09:36   
...                              ...                 ...   
3917  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   
3917  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   
3917  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   
3917  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   
3917  https://www.faz.net/-gzk-bhx0g 2023-11-13 18:29:46   

                                                  title  \
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
0     2. Bundesliga: Hertha verpasst mit 2:2 gegen K...   
...                                                 ...   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   
3917     „Happy New Ears“: 30 Jahre öffentliches Proben   

                                              introText  \
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
0     Hertha BSC dreht das Spiel gegen den Karlsruhe...   
...                                                 ...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   
3917  Man darf ruhig merken, wie schwer das ist: Bez...   

                                             paragraphs       source  \
0     Hertha BSC bleibt in der zweiten Fußball-Bunde...  Quelle: sid   
0     Fabian Reese (29.) und Florian Niederlechner (...  Quelle: sid   
0     Der Karlsruher SC startete überraschend selbst...  Quelle: sid   
0     In Halbzeit zwei zeigte Karlsruhe eine gute Re...  Quelle: sid   
0     Hertha BSC bleibt in der zweiten Fußball-Bunde...  Quelle: sid   
...                                                 ...          ...   
3917  „Zenders Idee war, dass wir an einem Abend ein...          NaN   
3917  Happy New Ears!“ ist der Neujahrswunsch des Ko...          NaN   
3917  „Zenders Idee war, dass wir an einem Abend ein...          NaN   
3917  Happy New Ears!“ ist der Neujahrswunsch des Ko...          NaN   
3917  „Zenders Idee war, dass wir an einem Abend ein...          NaN   

              author hrefAuthor  
0                NaN        NaN  
0                NaN        NaN  
0                NaN        NaN  
0                NaN        NaN  
0                NaN        NaN  
...              ...        ...  
3917  Doris Kösterke        NaN  
3917  Doris Kösterke        NaN  
3917  Doris Kösterke        NaN  
3917  Doris Kösterke        NaN 

In [20]:
profile = ProfileReport(df_exploded, title="Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]